In [1]:
import math
from ortools.constraint_solver import routing_enums_pb2
from ortools.constraint_solver import pywrapcp

In [2]:
import pandas as pd
pd.options.mode.chained_assignment = None  # default='warn'

import os

import haversine as hs

from datetime import datetime, timedelta

import numpy as np

In [3]:
from IPython.display import display

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

In [4]:
#import warnings
#warnings.filterwarnings("ignore")

In [5]:
distances = pd.read_csv('Circuit_Distances.csv', index_col=0)

distances

bahrain    jeddah  albert_park  shanghai      baku     miami  \
bahrain            0.00   1258.43     12112.63   6804.82   1595.70  12185.63   
jeddah          1258.43      0.00     12817.12   8062.08   2317.68  11605.63   
albert_park    12112.63  12817.12         0.00   8078.46  12989.08  15594.50   
shanghai        6804.82   8062.08      8078.46      0.00   6336.88  13248.55   
baku            1595.70   2317.68     12989.08   6336.88      0.00  11015.93   
miami          12185.63  11605.63     15594.50  13248.55  11015.93      0.00   
imola           4018.27   3559.50     16086.36   8986.37   3135.79   8172.92   
monaco          4332.65   3810.52     16422.24   9302.00   3484.89   7870.83   
catalunya       4710.93   4087.37     16823.35   9779.98   3946.50   7536.29   
villeneuve     10258.97   9929.43     16741.10  11342.35   8930.53   2253.88   
red_bull_ring   3910.84   3585.08     15878.75   8611.28   2890.55   8278.97   
silverstone     5158.08   4815.75     16947.24   9175.17   4030.59   7043.58   
hungaroring     3628.99   3387.79     15546.43   8302.58   2557.38   8573.80   
spa             4640.39   4307.69     16511.75   8926.20   3545.36   7556.53   
zandvoort       4805.05   4515.10     16572.56   8867.67   3652.58   7408.92   
monza           4242.73   3797.55     16288.08   9058.02   3314.42   7945.20   
marina_bay      6327.19   7353.82      6057.69   3806.81   6946.64  16953.20   
suzuka          8054.34   9293.32      8129.72   1477.81   7342.55  12224.22   
losail           112.11   1329.13     12000.56   6741.58   1661.51  12295.53   
americas       12908.78  12632.62     14286.08  12043.14  11489.38   1767.69   
rodriguez      13990.13  13574.58     13563.81  12920.89  12631.93   2064.12   
interlagos     11813.59  10555.63     13062.93  18553.96  12217.83   6596.17   
vegas          12943.28  13047.49     13131.15  10488.07  11373.52   3492.74   
yas_marina       446.84   1615.85     11674.76   6494.10   1823.13  12600.10   

                  imola    monaco  catalunya  villeneuve  red_bull_ring  \
bahrain         4018.27   4332.65    4710.93    10258.97        3910.84   
jeddah          3559.50   3810.52    4087.37     9929.43        3585.08   
albert_park    16086.36  16422.24   16823.35    16741.10       15878.75   
shanghai        8986.37   9302.00    9779.98    11342.35        8611.28   
baku            3135.79   3484.89    3946.50     8930.53        2890.55   
miami           8172.92   7870.83    7536.29     2253.88        8278.97   
imola              0.00    349.98     828.38     6372.27         397.58   
monaco           349.98      0.00     485.64     6121.74         690.95   
catalunya        828.38    485.64       0.00     5891.51        1173.27   
villeneuve      6372.27   6121.74    5891.51        0.00        6390.49   
red_bull_ring    397.58    690.95    1173.27     6390.49           0.00   
silverstone     1273.39   1119.23    1194.50     5137.22        1254.64   
hungaroring      683.89   1012.39    1497.97     6644.71         339.79   
spa              803.27    753.28    1026.45     5655.01         735.75   
zandvoort       1038.66    985.59    1215.20     5470.23         930.58   
monza            238.09    255.69     722.01     6134.60         456.50   
marina_bay     10077.87  10425.06   10873.36    14805.77        9834.15   
suzuka          9598.52   9874.96   10323.61    10584.02        9203.99   
losail          4129.25   4444.17    4822.99    10362.82        4019.64   
americas        9074.91   8824.30    8582.43     2703.19        9083.35   
rodriguez      10054.68   9778.21    9487.42     3731.54       10104.64   
interlagos      9612.48   9306.38    8834.87     8159.68        9994.67   
vegas           9592.05   9413.94    9288.44     3612.76        9494.93   
yas_marina      4443.94   4763.03    5148.63    10635.91        4321.13   

               silverstone  hungaroring       spa  zandvoort     monza  \
bahrain            5158.08      3628.99   4640.39    4805.05   42

In [6]:
distances_array = distances.to_numpy()

print(distances_array)

[[    0.    1258.43 12112.63  6804.82  1595.7  12185.63  4018.27  4332.65
   4710.93 10258.97  3910.84  5158.08  3628.99  4640.39  4805.05  4242.73
   6327.19  8054.34   112.11 12908.78 13990.13 11813.59 12943.28   446.84]
 [ 1258.43     0.   12817.12  8062.08  2317.68 11605.63  3559.5   3810.52
   4087.37  9929.43  3585.08  4815.75  3387.79  4307.69  4515.1   3797.55
   7353.82  9293.32  1329.13 12632.62 13574.58 10555.63 13047.49  1615.85]
 [12112.63 12817.12     0.    8078.46 12989.08 15594.5  16086.36 16422.24
  16823.35 16741.1  15878.75 16947.24 15546.43 16511.75 16572.56 16288.08
   6057.69  8129.72 12000.56 14286.08 13563.81 13062.93 13131.15 11674.76]
 [ 6804.82  8062.08  8078.46     0.    6336.88 13248.55  8986.37  9302.
   9779.98 11342.35  8611.28  9175.17  8302.58  8926.2   8867.67  9058.02
   3806.81  1477.81  6741.58 12043.14 12920.89 18553.96 10488.07  6494.1 ]
 [ 1595.7   2317.68 12989.08  6336.88     0.   11015.93  3135.79  3484.89
   3946.5   8930.53  2890.55  4030.5

In [7]:
distances_int = np.rint(distances_array)

distances_int = distances_int.astype(np.int64)

print(distances_int)

[[    0  1258 12113  6805  1596 12186  4018  4333  4711 10259  3911  5158
   3629  4640  4805  4243  6327  8054   112 12909 13990 11814 12943   447]
 [ 1258     0 12817  8062  2318 11606  3560  3811  4087  9929  3585  4816
   3388  4308  4515  3798  7354  9293  1329 12633 13575 10556 13047  1616]
 [12113 12817     0  8078 12989 15594 16086 16422 16823 16741 15879 16947
  15546 16512 16573 16288  6058  8130 12001 14286 13564 13063 13131 11675]
 [ 6805  8062  8078     0  6337 13249  8986  9302  9780 11342  8611  9175
   8303  8926  8868  9058  3807  1478  6742 12043 12921 18554 10488  6494]
 [ 1596  2318 12989  6337     0 11016  3136  3485  3946  8931  2891  4031
   2557  3545  3653  3314  6947  7343  1662 11489 12632 12218 11374  1823]
 [12186 11606 15594 13249 11016     0  8173  7871  7536  2254  8279  7044
   8574  7557  7409  7945 16953 12224 12296  1768  2064  6596  3493 12600]
 [ 4018  3560 16086  8986  3136  8173     0   350   828  6372   398  1273
    684   803  1039   238 10078 

In [8]:
def create_data_model():
    data = {}
    data['distance_matrix'] = distances_int
    data['num_vehicles'] = 1
    data['depot'] = 0
    return data

In [9]:
data = create_data_model()
manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']), data['num_vehicles'], data['depot'])
routing = pywrapcp.RoutingModel(manager)

In [10]:
def distance_callback(from_index, to_index):
    from_node = manager.IndexToNode(from_index)
    to_node = manager.IndexToNode(to_index)
    return data['distance_matrix'][from_node][to_node]

transit_callback_index = routing.RegisterTransitCallback(distance_callback)

In [11]:
routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)

In [12]:
search_parameters = pywrapcp.DefaultRoutingSearchParameters()
#search_parameters.first_solution_strategy = (routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)

search_parameters.local_search_metaheuristic = (routing_enums_pb2.LocalSearchMetaheuristic.GUIDED_LOCAL_SEARCH)
search_parameters.time_limit.seconds = 30
search_parameters.log_search = True

In [13]:
def print_solution(manager, routing, solution):
    print('Objective: {} kms'.format(solution.ObjectiveValue()))
    index = routing.Start(0)
    plan_output = 'Route for vehicle 0:\n'
    route_distance = 0
    while not routing.IsEnd(index):
        plan_output += ' {} ->'.format(manager.IndexToNode(index))
        previous_index = index
        index = solution.Value(routing.NextVar(index))
        route_distance += routing.GetArcCostForVehicle(previous_index, index, 0)
    plan_output += ' {}\n'.format(manager.IndexToNode(index))
    print(plan_output)
    plan_output += 'Route distance: {}miles\n'.format(route_distance)

In [14]:
solution = routing.SolveWithParameters(search_parameters)

I0000 00:00:1690383400.419459       1 search.cc:265] Start search (memory used = 135.45 MB)
I0000 00:00:1690383400.419546       1 search.cc:265] Root node processed (time = 0 ms, constraints = 104, memory used = 135.54 MB)
I0000 00:00:1690383400.421069       1 search.cc:265] Solution #0 (68502, time = 1 ms, branches = 34, failures = 1, depth = 33, memory used = 135.68 MB, limit = 0%)
I0000 00:00:1690383400.421920       1 search.cc:265] Solution #1 (68479, objective maximum = 68502, time = 2 ms, branches = 38, failures = 3, depth = 33, LinKernighan, neighbors = 1, filtered neighbors = 1, accepted neighbors = 1, memory used = 135.71 MB, limit = 0%)
I0000 00:00:1690383400.422104       1 search.cc:265] Solution #2 (68102, objective maximum = 68502, time = 2 ms, branches = 43, failures = 5, depth = 33, LinKernighan, neighbors = 2, filtered neighbors = 2, accepted neighbors = 2, memory used = 135.71 MB, limit = 0%)
I0000 00:00:1690383400.423281       1 search.cc:265] Solution #3 (64344, obje

I0000 00:00:1690383400.668564       1 search.cc:265] Solution #139 (62625, objective minimum = 62402, objective maximum = 82006, time = 249 ms, branches = 867, failures = 387, depth = 33, TwoOpt, neighbors = 95040, filtered neighbors = 139, accepted neighbors = 139, memory used = 135.91 MB, limit = 0%)
I0000 00:00:1690383400.668727       1 search.cc:265] Solution #140 (62402, objective maximum = 82006, time = 249 ms, branches = 875, failures = 389, depth = 33, TwoOpt, neighbors = 95052, filtered neighbors = 140, accepted neighbors = 140, memory used = 135.91 MB, limit = 0%)
I0000 00:00:1690383400.673024       1 search.cc:265] Solution #141 (62625, objective minimum = 62402, objective maximum = 82006, time = 253 ms, branches = 883, failures = 394, depth = 33, TwoOpt, neighbors = 96817, filtered neighbors = 141, accepted neighbors = 141, memory used = 135.91 MB, limit = 0%)
I0000 00:00:1690383400.673153       1 search.cc:265] Solution #142 (62402, objective maximum = 82006, time = 253 ms

I0000 00:00:1690383400.899528       1 search.cc:265] Solution #275 (62857, objective minimum = 62402, objective maximum = 82006, time = 480 ms, branches = 1672, failures = 752, depth = 33, OrOpt<1>, neighbors = 180623, filtered neighbors = 275, accepted neighbors = 275, memory used = 136.05 MB, limit = 1%)
I0000 00:00:1690383400.899843       1 search.cc:265] Solution #276 (62767, objective minimum = 62402, objective maximum = 82006, time = 480 ms, branches = 1676, failures = 754, depth = 33, OrOpt<1>, neighbors = 180646, filtered neighbors = 276, accepted neighbors = 276, memory used = 136.05 MB, limit = 1%)
I0000 00:00:1690383400.903444       1 search.cc:265] Solution #277 (62948, objective minimum = 62402, objective maximum = 82006, time = 483 ms, branches = 1683, failures = 756, depth = 33, TwoOpt, neighbors = 182182, filtered neighbors = 277, accepted neighbors = 277, memory used = 136.05 MB, limit = 1%)
I0000 00:00:1690383400.903940       1 search.cc:265] Solution #278 (62627, obj

I0000 00:00:1690383401.117218       1 search.cc:265] Solution #387 (63484, objective minimum = 62402, objective maximum = 82006, time = 697 ms, branches = 2347, failures = 1063, depth = 33, OrOpt<1>, neighbors = 258247, filtered neighbors = 387, accepted neighbors = 387, memory used = 136.09 MB, limit = 2%)
I0000 00:00:1690383401.117413       1 search.cc:265] Solution #388 (63436, objective minimum = 62402, objective maximum = 82006, time = 697 ms, branches = 2353, failures = 1065, depth = 33, OrOpt<1>, neighbors = 258248, filtered neighbors = 388, accepted neighbors = 388, memory used = 136.09 MB, limit = 2%)
I0000 00:00:1690383401.117666       1 search.cc:265] Solution #389 (63456, objective minimum = 62402, objective maximum = 82006, time = 698 ms, branches = 2357, failures = 1067, depth = 33, OrOpt<1>, neighbors = 258272, filtered neighbors = 389, accepted neighbors = 389, memory used = 136.09 MB, limit = 2%)
I0000 00:00:1690383401.120197       1 search.cc:265] Solution #390 (63383

I0000 00:00:1690383401.303736       1 search.cc:265] Solution #503 (66479, objective minimum = 62402, objective maximum = 82006, time = 884 ms, branches = 3012, failures = 1358, depth = 33, TwoOpt, neighbors = 319790, filtered neighbors = 503, accepted neighbors = 503, memory used = 136.26 MB, limit = 2%)
I0000 00:00:1690383401.304006       1 search.cc:265] Solution #504 (66800, objective minimum = 62402, objective maximum = 82006, time = 884 ms, branches = 3016, failures = 1360, depth = 33, TwoOpt, neighbors = 319791, filtered neighbors = 504, accepted neighbors = 504, memory used = 136.26 MB, limit = 2%)
I0000 00:00:1690383401.304568       1 search.cc:265] Solution #505 (67295, objective minimum = 62402, objective maximum = 82006, time = 885 ms, branches = 3021, failures = 1362, depth = 33, TwoOpt, neighbors = 319932, filtered neighbors = 505, accepted neighbors = 505, memory used = 136.26 MB, limit = 2%)
I0000 00:00:1690383401.305738       1 search.cc:265] Solution #506 (66800, obje

...

I0000 00:00:1690383429.705755       1 search.cc:265] Solution #16395 (71410, objective minimum = 62402, objective maximum = 102945, time = 29286 ms, branches = 93802, failures = 41641, depth = 33, OrOpt<1>, neighbors = 8683147, filtered neighbors = 16395, accepted neighbors = 16395, memory used = 136.75 MB, limit = 97%)
I0000 00:00:1690383429.711078       1 search.cc:265] Solution #16396 (72420, objective minimum = 62402, objective maximum = 102945, time = 29291 ms, branches = 93810, failures = 41646, depth = 33, OrOpt<1>, neighbors = 8684899, filtered neighbors = 16396, accepted neighbors = 16396, memory used = 136.75 MB, limit = 97%)
I0000 00:00:1690383429.711784       1 search.cc:265] Solution #16397 (73508, objective minimum = 62402, objective maximum = 102945, time = 29292 ms, branches = 93816, failures = 41648, depth = 33, OrOpt<1>, neighbors = 8684966, filtered neighbors = 16397, accepted neighbors = 16397, memory used = 136.75 MB, limit = 97%)
I0000 00:00:1690383429.712315     

I0000 00:00:1690383429.916771       1 search.cc:265] Solution #16491 (73149, objective minimum = 62402, objective maximum = 102945, time = 29497 ms, branches = 94364, failures = 41893, depth = 33, OrOpt<1>, neighbors = 8738446, filtered neighbors = 16491, accepted neighbors = 16491, memory used = 136.75 MB, limit = 98%)
I0000 00:00:1690383429.917385       1 search.cc:265] Solution #16492 (74193, objective minimum = 62402, objective maximum = 102945, time = 29497 ms, branches = 94369, failures = 41895, depth = 33, OrOpt<1>, neighbors = 8738469, filtered neighbors = 16492, accepted neighbors = 16492, memory used = 136.75 MB, limit = 98%)
I0000 00:00:1690383429.918786       1 search.cc:265] Solution #16493 (74231, objective minimum = 62402, objective maximum = 102945, time = 29499 ms, branches = 94373, failures = 41897, depth = 33, OrOpt<1>, neighbors = 8738829, filtered neighbors = 16493, accepted neighbors = 16493, memory used = 136.75 MB, limit = 98%)
I0000 00:00:1690383429.919363     

I0000 00:00:1690383430.130794       1 search.cc:265] Solution #16576 (70884, objective minimum = 62402, objective maximum = 102945, time = 29711 ms, branches = 94851, failures = 42111, depth = 33, TwoOpt, neighbors = 8797777, filtered neighbors = 16576, accepted neighbors = 16576, memory used = 136.76 MB, limit = 99%)
I0000 00:00:1690383430.136062       1 search.cc:265] Solution #16577 (63132, objective minimum = 62402, objective maximum = 102945, time = 29716 ms, branches = 94860, failures = 42116, depth = 33, TwoOpt, neighbors = 8799522, filtered neighbors = 16577, accepted neighbors = 16577, memory used = 136.76 MB, limit = 99%)
I0000 00:00:1690383430.142444       1 search.cc:265] Solution #16578 (70884, objective minimum = 62402, objective maximum = 102945, time = 29722 ms, branches = 94868, failures = 42121, depth = 33, TwoOpt, neighbors = 8801288, filtered neighbors = 16578, accepted neighbors = 16578, memory used = 136.76 MB, limit = 99%)
I0000 00:00:1690383430.143001       1 se

Objective: 62402 kms
Route for vehicle 0:
 0 -> 1 -> 12 -> 10 -> 6 -> 15 -> 7 -> 8 -> 13 -> 14 -> 11 -> 9 -> 22 -> 19 -> 20 -> 5 -> 21 -> 2 -> 16 -> 3 -> 17 -> 4 -> 23 -> 18 -> 0



I0000 00:00:1690383430.359687       1 search.cc:265] Solution #16683 (70406, objective minimum = 62402, objective maximum = 102945, time = 29940 ms, branches = 95469, failures = 42388, depth = 33, TwoOpt, neighbors = 8858649, filtered neighbors = 16683, accepted neighbors = 16683, memory used = 136.76 MB, limit = 99%)
I0000 00:00:1690383430.364748       1 search.cc:265] Solution #16684 (74297, objective minimum = 62402, objective maximum = 102945, time = 29945 ms, branches = 95478, failures = 42393, depth = 33, TwoOpt, neighbors = 8860397, filtered neighbors = 16684, accepted neighbors = 16684, memory used = 136.76 MB, limit = 99%)
I0000 00:00:1690383430.365276       1 search.cc:265] Solution #16685 (70406, objective minimum = 62402, objective maximum = 102945, time = 29945 ms, branches = 95482, failures = 42395, depth = 33, TwoOpt, neighbors = 8860398, filtered neighbors = 16685, accepted neighbors = 16685, memory used = 136.76 MB, limit = 99%)
I0000 00:00:1690383430.367031       1 se

In [23]:
if solution:
    print_solution(manager, routing, solution)

Objective: 62402 kms
Route for vehicle 0:
 0 -> 1 -> 12 -> 10 -> 6 -> 15 -> 7 -> 8 -> 13 -> 14 -> 11 -> 9 -> 22 -> 19 -> 20 -> 5 -> 21 -> 2 -> 16 -> 3 -> 17 -> 4 -> 23 -> 18 -> 0



In [15]:
def get_routes(solution, routing, manager):
    routes = []
    for route_nbr in range(routing.vehicles()):
        index = routing.Start(route_nbr)
        route = [manager.IndexToNode(index)]
        while not routing.IsEnd(index):
            index = solution.Value(routing.NextVar(index))
            route.append(manager.IndexToNode(index))
        routes.append(route)
    return routes

In [16]:
routes = get_routes(solution, routing, manager)
for i, route in enumerate(routes):
    print('Route', i, route)

Route 0 [0, 1, 12, 10, 6, 15, 7, 8, 13, 14, 11, 9, 22, 19, 20, 5, 21, 2, 16, 3, 17, 4, 23, 18, 0]


In [17]:
circuits = distances.columns.tolist()

print(circuits)

['bahrain', 'jeddah', 'albert_park', 'shanghai', 'baku', 'miami', 'imola', 'monaco', 'catalunya', 'villeneuve', 'red_bull_ring', 'silverstone', 'hungaroring', 'spa', 'zandvoort', 'monza', 'marina_bay', 'suzuka', 'losail', 'americas', 'rodriguez', 'interlagos', 'vegas', 'yas_marina']


In [24]:
for i in route:
    print(i, circuits[i])

0 bahrain
18 losail
23 yas_marina
3 shanghai
17 suzuka
16 marina_bay
2 albert_park
21 interlagos
5 miami
20 rodriguez
19 americas
22 vegas
9 villeneuve
11 silverstone
14 zandvoort
13 spa
8 catalunya
7 monaco
15 monza
6 imola
10 red_bull_ring
12 hungaroring
4 baku
1 jeddah
0 bahrain


In [18]:
for i in route:
    print(i, circuits[i])

0 bahrain
1 jeddah
12 hungaroring
10 red_bull_ring
6 imola
15 monza
7 monaco
8 catalunya
13 spa
14 zandvoort
11 silverstone
9 villeneuve
22 vegas
19 americas
20 rodriguez
5 miami
21 interlagos
2 albert_park
16 marina_bay
3 shanghai
17 suzuka
4 baku
23 yas_marina
18 losail
0 bahrain


In [19]:
high = 0

for i in range(0, len(route)-1):
    loc1 = circuits[route[i]]
    loc2 = circuits[route[i+1]]
    dist = distances.loc[loc1, loc2]
    print(loc1, loc2, dist)
    
    if dist > high:
        max1 = i
        max2 = i+1
        high = dist
        
print()
print(max1, max2, high)
print(route[max1], route[max2])

bahrain jeddah 1258.43
jeddah hungaroring 3387.79
hungaroring red_bull_ring 339.79
red_bull_ring imola 397.58
imola monza 238.09
monza monaco 255.69
monaco catalunya 485.64
catalunya spa 1026.45
spa zandvoort 238.6
zandvoort silverstone 379.97
silverstone villeneuve 5137.22
villeneuve vegas 3612.76
vegas americas 1759.61
americas rodriguez 1201.87
rodriguez miami 2064.12
miami interlagos 6596.17
interlagos albert_park 13062.93
albert_park marina_bay 6057.69
marina_bay shanghai 3806.81
shanghai suzuka 1477.81
suzuka baku 7342.55
baku yas_marina 1823.13
yas_marina losail 337.14
losail bahrain 112.11

16 17 13062.93
21 2


In [20]:
least = route[max2:-1] + route[:max1+1]

print(len(least), least)

24 [2, 16, 3, 17, 4, 23, 18, 0, 1, 12, 10, 6, 15, 7, 8, 13, 14, 11, 9, 22, 19, 20, 5, 21]


In [21]:
for i in least:
    print(i, circuits[i])

2 albert_park
16 marina_bay
3 shanghai
17 suzuka
4 baku
23 yas_marina
18 losail
0 bahrain
1 jeddah
12 hungaroring
10 red_bull_ring
6 imola
15 monza
7 monaco
8 catalunya
13 spa
14 zandvoort
11 silverstone
9 villeneuve
22 vegas
19 americas
20 rodriguez
5 miami
21 interlagos


In [22]:
tot = 0

for i in range(0, len(least)-1):
    loc1 = circuits[least[i]]
    loc2 = circuits[least[i+1]]
    
    tot = tot + distances.loc[loc1, loc2]
    
print(round(tot, 2))

49381.89


In [22]:
tot = 0

for i in range(0, len(least)-1):
    loc1 = circuits[least[i]]
    loc2 = circuits[least[i+1]]
    
    tot = tot + distances.loc[loc1, loc2]
    
print(round(tot, 2))

49337.02
